In [57]:
import findspark
findspark.init()

import pyspark
print(pyspark.__version__)

import sys
from pyspark import SparkContext, SparkConf
from pyspark.sql import SparkSession
import json 

import numpy as np
import pandas as pd
from matplotlib import pylab as plt
import matplotlib.cm as cm
%matplotlib inline 

from sklearn.metrics.pairwise import pairwise_distances,cosine_similarity

import warnings
warnings.filterwarnings('ignore')

3.0.0.dev2


In [2]:
# sc = SparkContext.getOrCreate(SparkConf().setMaster("local[*]"))
spark = SparkSession.builder\
                    .master("local[*]")\
                    .appName("Project")\
                    .config(conf=SparkConf())\
                    .getOrCreate()
                    
sc = spark.sparkContext

# conf = SparkConf()
# sc = SparkContext(conf=conf)

In [3]:
Movies_df = spark.read.csv('M_updated.csv', header = True)

In [8]:
Movies_df.show(1)

+---+-------+----------------+--------------------+------+------+------+--------+------------+--------+
|_c0|MovieID|           Title|               Genre|UserID|Rating|Gender|     Age|  Occupation|Zip-code|
+---+-------+----------------+--------------------+------+------+------+--------+------------+--------+
|  0|      1|Toy Story (1995)|Animation|Childre...|     1|     5|Female|Under 18|K-12 student|   48067|
+---+-------+----------------+--------------------+------+------+------+--------+------------+--------+
only showing top 1 row



In [11]:
Movies_df.printSchema()

root
 |-- _c0: string (nullable = true)
 |-- MovieID: string (nullable = true)
 |-- Title: string (nullable = true)
 |-- Genre: string (nullable = true)
 |-- UserID: string (nullable = true)
 |-- Rating: string (nullable = true)
 |-- Gender: string (nullable = true)
 |-- Age: string (nullable = true)
 |-- Occupation: string (nullable = true)
 |-- Zip-code: string (nullable = true)



In [2]:
Movies_pd_df = pd.read_csv('M_updated.csv')

In [3]:
Movies_pd_df.head(2)

Unnamed: 0  MovieID              Title  \
0           0        1   Toy Story (1995)   
1           1       48  Pocahontas (1995)   

                                  Genre  UserID  Rating  Gender       Age  \
0           Animation|Children's|Comedy       1       5  Female  Under 18   
1  Animation|Children's|Musical|Romance       1       5  Female  Under 18   

     Occupation Zip-code  
0  K-12 student    48067  
1  K-12 student    48067

In [4]:
len(Movies_pd_df)

1000209

In [15]:
Movies_pd_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000209 entries, 0 to 1000208
Data columns (total 10 columns):
Unnamed: 0    1000209 non-null int64
MovieID       1000209 non-null int64
Title         1000209 non-null object
Genre         1000209 non-null object
UserID        1000209 non-null int64
Rating        1000209 non-null int64
Gender        1000209 non-null object
Age           1000209 non-null object
Occupation    1000209 non-null object
Zip-code      1000209 non-null object
dtypes: int64(4), object(6)
memory usage: 76.3+ MB


In [49]:
df_m = Movies_pd_df.sample(10)

In [89]:
# df_m = df_m.drop(['Unnamed: 0'],axis=1).reset_index(drop=True)
df_m.MovieID = [1,2,3,4,5,2,1,3,4,7]
df_m.UserID = [1,1,1,1,1,2,2,2,2,2]
df_m.Gender = ['Male','Male','Male','Male','Male',
               'Female','Female','Female','Female','Female']
df_m.Occupation = ['programmer','programmer','programmer','programmer',
                   'programmer','self-employed','self-employed',
                   'self-employed','self-employed','self-employed']
df_m.Age = ['25-34','25-34','25-34','25-34','25-34',
            '50-55','50-55','50-55','50-55','50-55']
df_m['Zip-code'] = [60611,60611,60611,60611,60611,30052,30052,30052,30052,30052]


In [90]:
df_m

MovieID                                Title                     Genre  \
0        1                     King Kong (1976)   Action|Adventure|Horror   
1        2                     Tombstone (1993)                   Western   
2        3  There's Something About Mary (1998)                    Comedy   
3        4                 All That Jazz (1979)                   Musical   
4        5                     True Grit (1969)         Adventure|Western   
5        2             Strictly Ballroom (1992)            Comedy|Romance   
6        1                   Player, The (1992)              Comedy|Drama   
7        3  There's Something About Mary (1998)                    Comedy   
8        4                   Dragonheart (1996)  Action|Adventure|Fantasy   
9        7        Much Ado About Nothing (1993)            Comedy|Romance   

   UserID  Rating  Gender    Age     Occupation  Zip-code  
0       1       5    Male  25-34     programmer     60611  
1       1       3    Male  25-34     programmer     60611  
2       1       4    Male  25-34     programmer     60611  
3       1       3    Male  25-34     programmer     60611  
4       1       5    Male  25-34     programmer     60611  
5       2       1  Female  50-55  self-employed     30052  
6       2       3  Female  50-55  self-employed     30052  
7       2       4  Female  50-55  self-employed     30052  
8       2       3  Female  50-55  self-employed     30052  
9       2       4  Female  50-55  self-employed     30052

In [92]:
df_movie = df_m[['MovieID','Title','Genre']].drop_duplicates(['MovieID'])
df_movie

MovieID                                Title                    Genre
0        1                     King Kong (1976)  Action|Adventure|Horror
1        2                     Tombstone (1993)                  Western
2        3  There's Something About Mary (1998)                   Comedy
3        4                 All That Jazz (1979)                  Musical
4        5                     True Grit (1969)        Adventure|Western
9        7        Much Ado About Nothing (1993)           Comedy|Romance

In [93]:
df_user = df_m[['UserID','Gender','Age','Occupation','Zip-code']].drop_duplicates(['UserID'])
df_user

UserID  Gender    Age     Occupation  Zip-code
0       1    Male  25-34     programmer     60611
5       2  Female  50-55  self-employed     30052

In [103]:
df_rating = df_m[['UserID','MovieID','Rating']]
df_rating

UserID  MovieID  Rating
0       1        1       5
1       1        2       3
2       1        3       4
3       1        4       3
4       1        5       5
5       2        2       1
6       2        1       3
7       2        3       4
8       2        4       3
9       2        7       4

In [182]:
MovieID = np.sort(df_m.MovieID.unique())
MovieID = np.asarray([1, 2, 3, 4, 5, 7, 8])
MovieID 

array([1, 2, 3, 4, 5, 7, 8])

In [122]:
df_rating_temp = df_rating[df_rating['UserID']==2].sort_values(by = 'MovieID')
df_rating_temp

UserID  MovieID  Rating
6       2        1       3
5       2        2       1
7       2        3       4
8       2        4       3
9       2        7       4

In [133]:
# x in df_rating_temp['MovieID'] # compare x with the index not values of dataframe
# x in df_rating_temp['MovieID'].values # compare x with the values of dataframe

MovieID_no_rating = [x for x in MovieID if x not in \
                         df_rating_temp['MovieID'].values]

MovieID_no_rating 

[5]

In [157]:
df_rating_temp.Rating.values.T

array([3, 1, 4, 3, 4], dtype=int64)

In [ ]:
# Movie_no_rating = [1,2,3]
# user_id = np.full_like(Movie_no_rating,df_rating_temp['UserID'].iloc[0])
# rating_missing = np.full_like(Movie_no_rating,0)
# user_no_rating = np.vstack((user_id,no_rating,rating_missing)).T
# user_no_rating

In [174]:
MovieID_no_rating = [5,8]
user_id = np.full_like(MovieID_no_rating,df_rating_temp['UserID'].iloc[0])
rating_missing = np.full_like(MovieID_no_rating,0)
user_no_rating = np.vstack((user_id,MovieID_no_rating,rating_missing)).T
user_no_rating
# user_rating = df_rating_temp.Rating.T

array([[2, 5, 0],
       [2, 8, 0]])

In [183]:
user_rating = np.vstack((df_rating_temp.values,user_no_rating))
user_rating

array([[2, 1, 3],
       [2, 2, 1],
       [2, 3, 4],
       [2, 4, 3],
       [2, 7, 4],
       [2, 5, 0],
       [2, 8, 0]], dtype=int64)

In [184]:
df_user_rating = pd.DataFrame(user_rating,columns=df_rating_temp.columns)
df_user_rating = df_temp.sort_values('MovieID')

In [185]:
df_temp

UserID  MovieID  Rating
0       2        1       3
1       2        2       1
2       2        3       4
3       2        4       3
5       2        5       0
4       2        7       4
6       2        8       0

In [196]:
rating_temp = df_user_rating['Rating'].values
rating_temp = np.hstack((df_rating_temp['UserID'].iloc[0],rating_temp))

In [197]:
rating_temp

array([2, 3, 1, 4, 3, 0, 4, 0], dtype=int64)

In [198]:
df_rating = pd.DataFrame(columns=['UserID',*MovieID])
df_rating = pd.DataFrame()


Empty DataFrame
Columns: [UserID, 1, 2, 3, 4, 5, 7, 8]
Index: []

In [202]:
df_rating_temp = pd.DataFrame(rating_temp.reshape(1,-1),
                              columns=df_rating.columns)

df_rating_temp 

UserID  1  2  3  4  5  7  8
0       2  3  1  4  3  0  4  0

In [203]:
df_rating_temp

UserID  1  2  3  4  5  7  8
0       2  3  1  4  3  0  4  0

In [204]:
df_rating.append(df_rating_temp,ignore_index=True)

UserID  1  2  3  4  5  7  8
0      2  3  1  4  3  0  4  0

In [5]:
def get_rating(df_movie_user):
    df = df_movie_user[['UserID','MovieID','Rating']]
    MovieID = np.sort(df.MovieID.unique())
    print('MovieID:{}\n'.format(MovieID))
    
    UserID = np.sort(df.UserID.unique())
    df_rating = pd.DataFrame(columns=['UserID',*MovieID])
    for user_id in UserID:
        df_temp = df[df['UserID']==user_id].sort_values(by = 'MovieID')
        
        MovieID_no_rating = [x for x in MovieID if x not in \
                                    df_temp['MovieID'].values]
        
        rating_missing = np.full_like(MovieID_no_rating,0)
        
        uid_missing = np.full_like(MovieID_no_rating,user_id)
        
        user_no_rating = np.vstack((uid_missing,
                                    MovieID_no_rating,
                                    rating_missing)).T   
        user_rating = np.vstack((df_temp.values,user_no_rating))
        
        df_user_rating = pd.DataFrame(user_rating,columns=df_temp.columns)
#         print(df_user_rating)
        
        df_user_rating = df_user_rating.sort_values('MovieID')
        
        rating_temp = df_user_rating['Rating'].values
        
        rating_temp = np.hstack((user_id,rating_temp))
        
        df_rating_temp = pd.DataFrame(rating_temp.reshape(1,-1),
                                       columns=df_rating.columns)
        df_rating = df_rating.append(df_rating_temp,ignore_index=True)
    return df_rating

In [227]:
# df_rating = get_rating(Movies_pd_df)


MovieID:[   1    2    3 ... 3950 3951 3952]

      UserID  MovieID  Rating
0          1        1       5
1          1       48       5
2          1      150       5
3          1      260       4
4          1      527       5
...      ...      ...     ...
3701       1     3948       0
3702       1     3949       0
3703       1     3950       0
3704       1     3951       0
3705       1     3952       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
0          1        1       5
53         1        2       0
54         1        3       0
55         1        4       0
56         1        5       0
...      ...      ...     ...
3701       1     3948       0
3702       1     3949       0
3703       1     3950       0
3704       1     3951       0
3705       1     3952       0

[3706 rows x 3 columns]
[5 0 0 ... 0 0 0]
[1 5 0 ... 0 0 0]
      UserID  MovieID  Rating
0          2       21       1
1          2       95       2
2          2      110       5
3          2      163       4

[3706 rows x 3 columns]
      UserID  MovieID  Rating
23        12        1       0
24        12        2       0
25        12        3       0
26        12        4       0
27        12        5       0
...      ...      ...     ...
3701      12     3948       0
3702      12     3949       0
3703      12     3950       0
3704      12     3951       0
3705      12     3952       0

[3706 rows x 3 columns]
[0 0 0 ... 0 0 0]
[12  0  0 ...  0  0  0]
      UserID  MovieID  Rating
0         13        2       3
1         13       10       3
2         13       21       3
3         13       50       4
4         13       60       2
...      ...      ...     ...
3701      13     3948       0
3702      13     3949       0
3703      13     3950       0
3704      13     3951       0
3705      13     3952       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
108       13        1       0
0         13        2       3
109       13        3       0
110       13        4       0
111       13  

      UserID  MovieID  Rating
0         24       50       5
1         24      110       4
2         24      153       4
3         24      175       4
4         24      208       1
...      ...      ...     ...
3701      24     3948       0
3702      24     3949       0
3703      24     3950       0
3704      24     3951       0
3705      24     3952       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
136       24        1       0
137       24        2       0
138       24        3       0
139       24        4       0
140       24        5       0
...      ...      ...     ...
3701      24     3948       0
3702      24     3949       0
3703      24     3950       0
3704      24     3951       0
3705      24     3952       0

[3706 rows x 3 columns]
[0 0 0 ... 0 0 0]
[24  0  0 ...  0  0  0]
      UserID  MovieID  Rating
0         25      110       3
1         25      150       4
2         25      157       3
3         25      223       5
4         25      260       5
...     

      UserID  MovieID  Rating
0         36        1       5
1         36        6       5
2         36        7       4
3         36       10       4
4         36       11       4
...      ...      ...     ...
3701      36     3947       0
3702      36     3948       0
3703      36     3949       0
3704      36     3950       0
3705      36     3951       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
0         36        1       5
351       36        2       0
352       36        3       0
353       36        4       0
354       36        5       0
...      ...      ...     ...
3702      36     3948       0
3703      36     3949       0
3704      36     3950       0
3705      36     3951       0
350       36     3952       5

[3706 rows x 3 columns]
[5 0 0 ... 0 0 5]
[36  5  0 ...  0  0  5]
      UserID  MovieID  Rating
0         37       47       1
1         37      236       4
2         37      252       5
3         37      339       3
4         37      356       4
...     

      UserID  MovieID  Rating
0         48        1       4
1         48        2       3
2         48        5       3
3         48        6       4
4         48        7       4
...      ...      ...     ...
3701      48     3947       0
3702      48     3949       0
3703      48     3950       0
3704      48     3951       0
3705      48     3952       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
0         48        1       4
1         48        2       3
598       48        3       0
599       48        4       0
2         48        5       3
...      ...      ...     ...
597       48     3948       3
3702      48     3949       0
3703      48     3950       0
3704      48     3951       0
3705      48     3952       0

[3706 rows x 3 columns]
[4 3 0 ... 0 0 0]
[48  4  3 ...  0  0  0]
      UserID  MovieID  Rating
0         49        1       5
1         49       13       4
2         49       21       3
3         49       89       4
4         49       95       2
...     

...

      UserID  MovieID  Rating
0       5992       24       4
1       5992       86       4
2       5992      317       2
3       5992      338       3
4       5992      356       5
...      ...      ...     ...
3701    5992     3948       0
3702    5992     3949       0
3703    5992     3950       0
3704    5992     3951       0
3705    5992     3952       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
67      5992        1       0
68      5992        2       0
69      5992        3       0
70      5992        4       0
71      5992        5       0
...      ...      ...     ...
3701    5992     3948       0
3702    5992     3949       0
3703    5992     3950       0
3704    5992     3951       0
3705    5992     3952       0

[3706 rows x 3 columns]
[0 0 0 ... 0 0 0]
[5992    0    0 ...    0    0    0]
      UserID  MovieID  Rating
0       5993       50       3
1       5993      594       4
2       5993      597       1
3       5993      903       4
4       5993      904     

      UserID  MovieID  Rating
0       6002       45       5
1       6002      101       4
2       6002      110       3
3       6002      111       3
4       6002      144       4
...      ...      ...     ...
3701    6002     3948       0
3702    6002     3949       0
3703    6002     3950       0
3704    6002     3951       0
3705    6002     3952       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
335     6002        1       0
336     6002        2       0
337     6002        3       0
338     6002        4       0
339     6002        5       0
...      ...      ...     ...
3701    6002     3948       0
3702    6002     3949       0
3703    6002     3950       0
3704    6002     3951       0
3705    6002     3952       0

[3706 rows x 3 columns]
[0 0 0 ... 0 0 0]
[6002    0    0 ...    0    0    0]
      UserID  MovieID  Rating
0       6003        6       4
1       6003       17       5
2       6003       21       4
3       6003       22       2
4       6003       32     

      UserID  MovieID  Rating
0       6012      382       4
1       6012      481       4
2       6012      592       1
3       6012     1198       3
4       6012     2283       2
...      ...      ...     ...
3701    6012     3948       0
3702    6012     3949       0
3703    6012     3950       0
3704    6012     3951       0
3705    6012     3952       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
23      6012        1       0
24      6012        2       0
25      6012        3       0
26      6012        4       0
27      6012        5       0
...      ...      ...     ...
3701    6012     3948       0
3702    6012     3949       0
3703    6012     3950       0
3704    6012     3951       0
3705    6012     3952       0

[3706 rows x 3 columns]
[0 0 0 ... 0 0 0]
[6012    0    0 ...    0    0    0]
      UserID  MovieID  Rating
0       6013        1       5
1       6013       28       3
2       6013       34       5
3       6013       50       1
4       6013       80     

      UserID  MovieID  Rating
0       6022        1       5
1       6022      110       3
2       6022      246       5
3       6022      260       5
4       6022      296       5
...      ...      ...     ...
3701    6022     3948       0
3702    6022     3949       0
3703    6022     3950       0
3704    6022     3951       0
3705    6022     3952       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
0       6022        1       5
48      6022        2       0
49      6022        3       0
50      6022        4       0
51      6022        5       0
...      ...      ...     ...
3701    6022     3948       0
3702    6022     3949       0
3703    6022     3950       0
3704    6022     3951       0
3705    6022     3952       0

[3706 rows x 3 columns]
[5 0 0 ... 0 0 0]
[6022    5    0 ...    0    0    0]
      UserID  MovieID  Rating
0       6023        6       5
1       6023       22       5
2       6023       42       2
3       6023       44       3
4       6023       47     

      UserID  MovieID  Rating
0       6032        1       4
1       6032       17       5
2       6032       34       5
3       6032      111       5
4       6032      246       5
...      ...      ...     ...
3701    6032     3948       0
3702    6032     3949       0
3703    6032     3950       0
3704    6032     3951       0
3705    6032     3952       0

[3706 rows x 3 columns]
      UserID  MovieID  Rating
0       6032        1       4
104     6032        2       0
105     6032        3       0
106     6032        4       0
107     6032        5       0
...      ...      ...     ...
3701    6032     3948       0
3702    6032     3949       0
3703    6032     3950       0
3704    6032     3951       0
3705    6032     3952       0

[3706 rows x 3 columns]
[4 0 0 ... 0 0 0]
[6032    4    0 ...    0    0    0]
      UserID  MovieID  Rating
0       6033      110       5
1       6033      260       4
2       6033      292       4
3       6033      349       5
4       6033      380     

In [10]:
df_rating.head(2)

UserID  1  2  3  4  5  6  7  8  9  ...  3943  3944  3945  3946  3947  3948  \
0       1  5  0  0  0  0  0  0  0  0  ...     0     0     0     0     0     0   
1       2  0  0  0  0  0  0  0  0  0  ...     0     0     0     0     0     0   

   3949  3950  3951  3952  
0     0     0     0     0  
1     0     0     0     0  

[2 rows x 3707 columns]

In [8]:
# df_rating.to_csv('./output/df_rating.csv',index=False)
df_rating = pd.read_csv('./output/df_rating.csv')

In [9]:
np.sort(Movies_pd_df.MovieID.unique()),np.sort(Movies_pd_df.UserID.unique())

(array([   1,    2,    3, ..., 3950, 3951, 3952], dtype=int64),
 array([   1,    2,    3, ..., 6038, 6039, 6040], dtype=int64))

In [27]:
Movies_pd_df.MovieID.unique().size,Movies_pd_df.UserID.unique().size

(3706, 6040)

#### Similarity based on sklearn  distance

In [17]:
Sample_df = Movies_pd_df.sample(n=20000)

In [18]:
Sample_df.head(2)

Unnamed: 0  MovieID  \
940236      940236     3118   
890476      890476     3868   

                                                    Title   Genre  UserID  \
940236                                 Tumbleweeds (1999)   Drama    4941   
890476  Naked Gun: From the Files of Police Squad!, Th...  Comedy    1409   

        Rating Gender    Age            Occupation Zip-code  
940236       3   Male    56+                writer    44281  
890476       5   Male  18-24  college/grad student    97215

In [19]:
from sklearn.model_selection import cross_validate as cv
from sklearn.model_selection import train_test_split

train_df, test_df = train_test_split(Sample_df, test_size=0.2)

In [20]:
# Create two user-item matrices for training and testing data
train_data_matrix = train_df[['UserID', 'MovieID', 'Rating']].to_numpy()
test_data_matrix = test_df[['UserID', 'MovieID', 'Rating']].to_numpy()

In [244]:
train_data_matrix

array([[5167,  671,    5],
       [2734, 2581,    3],
       [3789, 2997,    5],
       ...,
       [5689, 2336,    4],
       [ 823,  898,    3],
       [3518, 3396,    5]], dtype=int64)

In [21]:
from sklearn.metrics.pairwise import pairwise_distances

# User Similarity Matrix
user_correlation = 1 - pairwise_distances(train_data_matrix, metric='correlation')
user_correlation[np.isnan(user_correlation)] = 0
# Item Similarity Matrix
item_correlation = 1 - pairwise_distances(train_data_matrix.T, metric='correlation')
item_correlation[np.isnan(item_correlation)] = 0

In [22]:
user_correlation.shape,item_correlation.shape

((16000, 16000), (3, 3))

In [39]:
# Function to predict ratings
def predict(ratings, similarity, type='user'):
    if type == 'user':
        mean_user_rating = ratings.mean(axis=1)
        # Use np.newaxis so that mean_user_rating has same format as ratings
        ratings_diff = (ratings - mean_user_rating[:, np.newaxis])
        pred = mean_user_rating[:, np.newaxis] + similarity.dot(ratings_diff)/ np.array([np.abs(similarity).sum(axis=1)]).T
    elif type == 'item':
        pred = ratings.dot(similarity) / np.array([np.abs(similarity).sum(axis=1)])
    return pred

In [43]:
from sklearn.metrics import mean_squared_error
from math import sqrt

# Function to calculate RMSE
def rmse(pred, actual):
    # Ignore nonzero terms.
    pred = pred[actual.nonzero()].flatten()
    actual = actual[actual.nonzero()].flatten()
    return sqrt(mean_squared_error(pred, actual))
# Predict ratings on the training data with both similarity score
user_prediction = predict(train_data_matrix, user_correlation, type='user')
item_prediction = predict(train_data_matrix, item_correlation, type='item')
# RMSE on the train data
print('User-based Collaborative Filtering RMSE: ' + str(rmse(user_prediction, train_data_matrix)))
print('Item-based Collaborative Filtering RMSE: ' + str(rmse(item_prediction, train_data_matrix)))


User-based Collaborative Filtering RMSE: 695.3600443064229
Item-based Collaborative Filtering RMSE: 151.74730429024274


#### 9.3 Collaborative Filtering
Example 9.1 : In Fig. 9.1 we see an example utility matrix, representing users’
ratings of movies on a 1–5 scale, with 5 the highest rating. Blanks represent
the situation where the user has not rated the movie. The movie names are
HP1, HP2, and HP3 for Harry Potter I, II, and III, TW for Twilight, and SW1,
SW2, and SW3 for Star Wars episodes 1, 2, and 3. The users are represented
by capital letters A through D.

**The utility matrix (rating matrix):**

In [10]:
rating_test = [[4,0,0,5,1,0,0],
               [5,5,4,0,0,0,0],
               [0,0,0,2,4,5,0],
               [0,3,0,0,0,0,3]]
print(rating_test)
df_test = pd.DataFrame(rating_test,columns=['HP1','HP2','HP3',
                                            'TW','SW1','SW2','SW3'])
df_test

[[4, 0, 0, 5, 1, 0, 0], [5, 5, 4, 0, 0, 0, 0], [0, 0, 0, 2, 4, 5, 0], [0, 3, 0, 0, 0, 0, 3]]


HP1  HP2  HP3  TW  SW1  SW2  SW3
0    4    0    0   5    1    0    0
1    5    5    4   0    0    0    0
2    0    0    0   2    4    5    0
3    0    3    0   0    0    0    3

**Jaccard similarity:**

In [11]:
jaccard_dist = pairwise_distances(df_test.values, metric='jaccard')

In [12]:
jaccard_similarity = 1 - jaccard_dist
jaccard_similarity

array([[1.  , 0.2 , 0.5 , 0.  ],
       [0.2 , 1.  , 0.  , 0.25],
       [0.5 , 0.  , 1.  , 0.  ],
       [0.  , 0.25, 0.  , 1.  ]])

**Cosine Similarity:**<br>
$\quad$scipy.spatial.distance.cosine<br>
$\quad$scipy.spatial.distance.cosine(u, v, w=None)<br>
$\quad$Compute the Cosine distance between $1-D$ arrays.<br>
The Cosine distance between $u$ and $v$, is defined as<br>
$\qquad 1- \frac{u\cdot v}{\parallel u\parallel_{2}\cdot \parallel v\parallel_{2}}$<br>
 where $\parallel u\parallel_{2}\cdot \parallel v\parallel_{2}$ is the dot product of $u$ and $v$.
 
 Parameters:<br>
$\quad u(N,)$: array_like,Input array.<br>

$\quad v(N,)$: array_like,Input array.<br>

$\quad w(N,)$: array_like, optional<br>
The weights for each value in $u$ and $v$. Default is None, which gives each value a weight of 1.0<br>

Returns:<br>
$\quad cosine$:double<br>
The Cosine distance between vectors $u$ and $v$.

In [13]:
cosine_dist =  pairwise_distances(df_test.values, metric='cosine')
cosine_dist

array([[0.        , 0.62013141, 0.67796941, 1.        ],
       [0.62013141, 0.        , 1.        , 0.56480586],
       [0.67796941, 1.        , 0.        , 1.        ],
       [1.        , 0.56480586, 1.        , 0.        ]])

In [14]:
cosine_similarity = 1 - cosine_dist
cosine_similarity

array([[1.        , 0.37986859, 0.32203059, 0.        ],
       [0.37986859, 1.        , 0.        , 0.43519414],
       [0.32203059, 0.        , 1.        , 0.        ],
       [0.        , 0.43519414, 0.        , 1.        ]])

**Correlation similarity:**

In [15]:
correlation_dist = pairwise_distances(df_test.values,metric='correlation')
print('correlation_dist:\n{}'.format(correlation_dist))
correlation_similarity = 1 - correlation_dist
correlation_similarity

correlation_dist:
[[0.         1.         1.06185567 1.45407661]
 [1.         0.         1.67792092 0.86427582]
 [1.06185567 1.67792092 0.         1.49948427]
 [1.45407661 0.86427582 1.49948427 0.        ]]


array([[ 1.        ,  0.        , -0.06185567, -0.45407661],
       [ 0.        ,  1.        , -0.67792092,  0.13572418],
       [-0.06185567, -0.67792092,  1.        , -0.49948427],
       [-0.45407661,  0.13572418, -0.49948427,  1.        ]])

***Similarity Scores***

In [30]:
ratings = df_test.values
ratings

array([[4, 0, 0, 5, 1, 0, 0],
       [5, 5, 4, 0, 0, 0, 0],
       [0, 0, 0, 2, 4, 5, 0],
       [0, 3, 0, 0, 0, 0, 3]], dtype=int64)

In [31]:
mean_user_rating = ratings.mean(axis=1)
print(mean_user_rating)

ratings_diff = (ratings - mean_user_rating[:, np.newaxis])
print('ratings_diff:\n',ratings_diff)

[1.42857143 2.         1.57142857 0.85714286]
ratings_diff:
 [[ 2.57142857 -1.42857143 -1.42857143  3.57142857 -0.42857143 -1.42857143
  -1.42857143]
 [ 3.          3.          2.         -2.         -2.         -2.
  -2.        ]
 [-1.57142857 -1.57142857 -1.57142857  0.42857143  2.42857143  3.42857143
  -1.57142857]
 [-0.85714286  2.14285714 -0.85714286 -0.85714286 -0.85714286 -0.85714286
   2.14285714]]


In [43]:
similarity = correlation_similarity
similarity

array([[ 1.        ,  0.        , -0.06185567, -0.45407661],
       [ 0.        ,  1.        , -0.67792092,  0.13572418],
       [-0.06185567, -0.67792092,  1.        , -0.49948427],
       [-0.45407661,  0.13572418, -0.49948427,  1.        ]])

In [ ]:
pred = mean_user_rating[:, np.newaxis] + \
       similarity.dot(ratings_diff)/ np.array([np.abs(similarity).sum(axis=1)]).T

In [35]:
similarity.dot(ratings_diff)

array([[ 3.05783886, -2.30439097, -0.94216114,  3.93412752, -0.18958382,
        -1.25143949, -2.30439097],
       [ 3.9489693 ,  4.35614183,  2.9489693 , -2.40687255, -3.76271439,
        -4.44063532, -0.64385817],
       [-3.3361194 , -4.58714953, -2.4107758 ,  1.99162954,  4.23905222,
         5.30090789, -1.19754492],
       [-0.83269204,  3.9836144 ,  0.84789022, -2.96435808, -2.14702018,
        -2.19242784,  3.30499351]])

In [42]:
np.abs(similarity).sum(axis=1).reshape(-1,1)

array([[1.51593228],
       [1.8136451 ],
       [2.23926086],
       [2.08928506]])

In [40]:
np.array([np.abs(similarity).sum(axis=1)]).T

array([[1.51593228],
       [1.8136451 ],
       [2.23926086],
       [2.08928506]])

In [ ]:
similarity = correlation_similarity

In [55]:
# axis = 0 ,vertical
df_T = df_test.T
print(df_T)
print()
print(df_T.mean(axis=1))
print(df_T.iloc[1] - 8/4)
df_T.sub(df_T.mean(axis=1),axis='index')


     0  1  2  3
HP1  4  5  0  0
HP2  0  5  0  3
HP3  0  4  0  0
TW   5  0  2  0
SW1  1  0  4  0
SW2  0  0  5  0
SW3  0  0  0  3

HP1    2.25
HP2    2.00
HP3    1.00
TW     1.75
SW1    1.25
SW2    1.25
SW3    0.75
dtype: float64
0   -2.0
1    3.0
2   -2.0
3    1.0
Name: HP2, dtype: float64


0     1     2     3
HP1  1.75  2.75 -2.25 -2.25
HP2 -2.00  3.00 -2.00  1.00
HP3 -1.00  3.00 -1.00 -1.00
TW   3.25 -1.75  0.25 -1.75
SW1 -0.25 -1.25  2.75 -1.25
SW2 -1.25 -1.25  3.75 -1.25
SW3 -0.75 -0.75 -0.75  2.25

In [48]:
# axis = 1, horizontal
print(df_test.mean(axis=1))
df_test.sub(df_test.mean(axis=1),axis='index')

0    1.428571
1    2.000000
2    1.571429
3    0.857143
dtype: float64


HP1       HP2       HP3        TW       SW1       SW2       SW3
0  2.571429 -1.428571 -1.428571  3.571429 -0.428571 -1.428571 -1.428571
1  3.000000  3.000000  2.000000 -2.000000 -2.000000 -2.000000 -2.000000
2 -1.571429 -1.571429 -1.571429  0.428571  2.428571  3.428571 -1.571429
3 -0.857143  2.142857 -0.857143 -0.857143 -0.857143 -0.857143  2.142857

In [18]:
10/7

1.4285714285714286